%pip install qbraid[azure]==0.9.6.dev20250425155658 qbraid-qir pasqal-cloud pulser-core pulser-simulation qiskit qiskit_algorithms qiskit_optimization cirq --quiet

In [1]:
import pandas as pd
import numpy as np
from qiskit_algorithms.utils import algorithm_globals
from qiskit_algorithms import QAOA, NumPyMinimumEigensolver
from qiskit_algorithms.optimizers import COBYLA
from qiskit.primitives import Sampler
from qiskit_optimization.algorithms import MinimumEigenOptimizer
from qiskit_optimization import QuadraticProgram

In [2]:
csv_path = "filtered_DLRM_trace.csv"
job_num = 2000
n = 20
gmax = 8
cmax = 256
mem_max = 1024
threshold = 0.4

df = pd.read_csv(csv_path, nrows=job_num, usecols=['app_name', 'cpu_request', 'gpu_request', 'memory_request'])
df["memory_request"] = df["memory_request"].round().astype(int)
print(df)

     app_name  cpu_request  gpu_request  memory_request
0      app_88           64            0             320
1      app_46           96            0             480
2      app_42          192            0             938
3      app_27           64            0             320
4      app_56           64            0             320
...       ...          ...          ...             ...
1995   app_87           64            0             320
1996   app_87           64            0             320
1997   app_14           48            0             240
1998   app_87           64            0             320
1999   app_87           64            0             320

[2000 rows x 4 columns]


In [3]:
alpha = 0.6  # Adjustable variable

# Create a dictionary to track the appearance count of each app_name
app_count = {}

def calculate_priority(app_name):
    if app_name not in app_count:
        app_count[app_name] = 1
        return 1  # First appearance, priority is 1
    else:
        app_count[app_name] += 1
        return alpha ** (app_count[app_name] - 1)  # Subsequent appearances

# Apply the function to calculate priority for each row
df['priority'] = df['app_name'].apply(calculate_priority)

print(df)

     app_name  cpu_request  gpu_request  memory_request       priority
0      app_88           64            0             320   1.000000e+00
1      app_46           96            0             480   1.000000e+00
2      app_42          192            0             938   1.000000e+00
3      app_27           64            0             320   1.000000e+00
4      app_56           64            0             320   1.000000e+00
...       ...          ...          ...             ...            ...
1995   app_87           64            0             320  3.463301e-123
1996   app_87           64            0             320  2.077980e-123
1997   app_14           48            0             240   2.799360e-02
1998   app_87           64            0             320  1.246788e-123
1999   app_87           64            0             320  7.480730e-124

[2000 rows x 5 columns]


In [4]:
print(df['priority'])

0        1.000000e+00
1        1.000000e+00
2        1.000000e+00
3        1.000000e+00
4        1.000000e+00
            ...      
1995    3.463301e-123
1996    2.077980e-123
1997     2.799360e-02
1998    1.246788e-123
1999    7.480730e-124
Name: priority, Length: 2000, dtype: float64


In [5]:
qp = QuadraticProgram()

# Add binary variables for each job-machine combination
for i in range(1, job_num + 1):
    for j in range(1, n + 1):
        qp.binary_var(f"job{i}machine{j}")

linear = {}
for i in range(1, job_num + 1):
    for j in range(1, n + 1):
        linear[f"job{i}machine{j}"] = -df.loc[i - 1, 'priority']
qp.minimize(linear=linear)
print(qp.prettyprint())


Problem name: 

Minimize
  -5.404696583114737e-40*job1000machine1
  - 5.404696583114737e-40*job1000machine10
  - 5.404696583114737e-40*job1000machine11
  - 5.404696583114737e-40*job1000machine12
  - 5.404696583114737e-40*job1000machine13
  - 5.404696583114737e-40*job1000machine14
  - 5.404696583114737e-40*job1000machine15
  - 5.404696583114737e-40*job1000machine16
  - 5.404696583114737e-40*job1000machine17
  - 5.404696583114737e-40*job1000machine18
  - 5.404696583114737e-40*job1000machine19
  - 5.404696583114737e-40*job1000machine2
  - 5.404696583114737e-40*job1000machine20
  - 5.404696583114737e-40*job1000machine3
  - 5.404696583114737e-40*job1000machine4
  - 5.404696583114737e-40*job1000machine5
  - 5.404696583114737e-40*job1000machine6
  - 5.404696583114737e-40*job1000machine7
  - 5.404696583114737e-40*job1000machine8
  - 5.404696583114737e-40*job1000machine9
  - 0.0013060694015999993*job1001machine1
  - 0.0013060694015999993*job1001machine10
  - 0.0013060694015999993*job1001machine

In [6]:
#GPU capacity constraint
for i in range(1, n + 1):
    machines = {}

    for j in range(1, job_num + 1):
        machines[f"job{j}machine{i}"] = df.loc[j - 1, 'gpu_request']

    #print(i, machines)

    qp.linear_constraint(
        linear=machines,
        sense="LE",
        rhs=gmax,
        name=f"gpu_capacity_{i}",
    )

#CPU capacity constraint
for i in range(1, n + 1):
    machines = {}
    for j in range(1, job_num + 1):
        machines[f"job{j}machine{i}"] = df.loc[j - 1, 'cpu_request']

    qp.linear_constraint(
        linear=machines,
        sense="LE",
        rhs=cmax,
        name=f"cpu_capacity_{i}",
    )

#Memory capacity constraint
# for i in range(1, n + 1):
#     machines = {}
#     for j in range(1, job_num + 1):
#         machines[f"job{j}machine{i}"] = df.loc[j - 1, 'memory_request']

#     qp.linear_constraint(
#         linear=machines,
#         sense="LE",
#         rhs=mem_max,
#         name=f"memory_capacity_{i}",
#     )

# Each job can only be assigned to one machine
for i in range(1, job_num + 1):
    linear = {}
    for j in range(1, n + 1):
        linear[f"job{i}machine{j}"] = 1

    qp.linear_constraint(
        linear=linear,
        sense="EQ",
        rhs=1,
        name=f"job_assignment_{i}",
    )

# Two jobs that take more than 30% of the GPU cannot be assigned to the same machine
for i in range(1, job_num + 1):
    for j in range(i + 1, job_num + 1):
        if df.loc[i - 1, 'gpu_request'] > gmax * 0.3 and df.loc[j - 1, 'gpu_request'] > gmax * threshold:
            for k in range(1, n + 1):
                qp.linear_constraint(
                    linear={f"job{i}machine{k}": 1, f"job{j}machine{k}": 1},
                    sense="LE",
                    rhs=1,
                    name=f"gpu_conflict_{i}_{j}_{k}",
                )

print(qp.prettyprint())


Problem name: 

Minimize
  -5.404696583114737e-40*job1000machine1
  - 5.404696583114737e-40*job1000machine10
  - 5.404696583114737e-40*job1000machine11
  - 5.404696583114737e-40*job1000machine12
  - 5.404696583114737e-40*job1000machine13
  - 5.404696583114737e-40*job1000machine14
  - 5.404696583114737e-40*job1000machine15
  - 5.404696583114737e-40*job1000machine16
  - 5.404696583114737e-40*job1000machine17
  - 5.404696583114737e-40*job1000machine18
  - 5.404696583114737e-40*job1000machine19
  - 5.404696583114737e-40*job1000machine2
  - 5.404696583114737e-40*job1000machine20
  - 5.404696583114737e-40*job1000machine3
  - 5.404696583114737e-40*job1000machine4
  - 5.404696583114737e-40*job1000machine5
  - 5.404696583114737e-40*job1000machine6
  - 5.404696583114737e-40*job1000machine7
  - 5.404696583114737e-40*job1000machine8
  - 5.404696583114737e-40*job1000machine9
  - 0.0013060694015999993*job1001machine1
  - 0.0013060694015999993*job1001machine10
  - 0.0013060694015999993*job1001machine

In [ ]:
qaoa_mes = QAOA(sampler=Sampler(), optimizer=COBYLA(), initial_point=[0.0, 0.0])
qaoa = MinimumEigenOptimizer(qaoa_mes)
qaoa_result = qaoa.solve(qp)
print(qaoa_result.prettyprint())